In [2]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler


In [3]:
merged = pd.read_csv(r'C:\Users\jerin\Downloads\lbnlbldg59\lbnlbldg59\lbnlbldg59.processed\LBNLBLDG59\clean_Bldg59_2018to2020\clean data\long_merge.csv')

zone = "47"

if zone in ["36", "37", "38", "39", "40", "41", "42", "64", "65", "66", "67", "68", "69", "70"]:
    rtu = "rtu_001"
    wing = "hvac_N"
elif zone in ["18", "25", "26", "45", "48", "55", "56", "61"]:
    rtu = "rtu_003"
    wing = "hvac_S"
elif zone in ["16", "17", "21", "22", "23", "24", "46", "47", "51", "52", "53", "54"]:
    rtu = "rtu_004"
    wing = "hvac_S"
else:
    rtu = "rtu_002"
    wing = "hvac_N"
#merged is the dataframe
sorted = merged[["date"]+[col for col in merged.columns if zone in col or rtu in col or wing in col]+["hp_hws_temp", "aru_001_cwr_temp" , "aru_001_cws_fr_gpm" ,"aru_001_cws_temp","aru_001_hwr_temp" ,"aru_001_hws_fr_gpm" ,"aru_001_hws_temp"]]
sorted

date  zone_047_hw_valve  rtu_004_sat_sp_tn  \
0        2018-01-01 00:00:00              100.0               69.0   
1        2018-01-01 00:01:00              100.0               69.0   
2        2018-01-01 00:02:00              100.0               69.0   
3        2018-01-01 00:03:00              100.0               69.0   
4        2018-01-01 00:04:00              100.0               69.0   
...                      ...                ...                ...   
2072149  2020-12-31 23:58:00              100.0               68.0   
2072150  2020-12-31 23:58:00              100.0               68.0   
2072151  2020-12-31 23:59:00              100.0               68.0   
2072152  2020-12-31 23:59:00              100.0               68.0   
2072153  2021-01-01 00:00:00              100.0               68.0   

         zone_047_temp  zone_047_fan_spd  rtu_004_fltrd_sa_flow_tn  \
0                 67.5              20.0                  9265.604   
1                 67.5              20.0                  9265.604   
2                 67.5              20.0                  9708.240   
3                 67.5              20.0                  9611.638   
4                 67.5              20.0                  9215.110   
...                ...               ...                       ...   
2072149           63.2              20.0                 18884.834   
2072150           63.2              20.0                 18884.834   
2072151           63.2              20.0                 19345.508   
2072152           63.2              20.0                 19345.508   
2072153           63.2              20.0                 18650.232   

         rtu_004_sa_temp  rtu_004_pa_static_stpt_tn  rtu_004_oa_flow_tn  \
0                   66.1                       0.06            0.000000   
1                   66.0                       0.06         6572.099162   
2                   66.1                       0.06         7628.832542   
3                   66.1                       0.06         7710.294617   
4                   66.0                       0.06         7139.184090   
...                  ...                        ...                 ...   
2072149             64.4                       0.06         2938.320000   
2072150             64.4                       0.06         2938.320000   
2072151             64.3                       0.06         3154.390000   
2072152             64.3                       0.06         3154.390000   
2072153             64.1                       0.06         3076.270000   

         rtu_004_oadmpr_pct  ...  zone_047_heating_sp  Unnamed: 47_y  \
0                      28.0  ...                  NaN            NaN   
1                      28.0  ...                  NaN            NaN   
2                      28.0  ...                  NaN            NaN   
3                      28.0  ...                  NaN            NaN   
4                      28.0  ...                  NaN            NaN   
...                     ...  ...                  ...            ...   
2072149                23.4  ...                 71.0           69.0   
2072150                23.4  ...                 71.0           69.0   
2072151                23.4  ...                 71.0           69.0   
2072152                23.4  ...                 71.0           69.0   
2072153                22.9  ...                 71.0           69.0   

            hvac_S  hp_hws_temp  aru_001_cwr_temp  aru_001_cws_fr_gpm  \
0              NaN         75.3               NaN                 NaN   
1              NaN         75.3               NaN                 NaN   
2              NaN         75.3               NaN                 NaN   
3              NaN         75.3               NaN                 NaN   
4              NaN         75.3               NaN                 NaN   
...            ...          ...               ...                 ...   
2072149  23.145000        123.8             56.25               5

In [100]:
correlation_matrix = sorted.loc[:, sorted.columns != 'date'].corr()
plt.figure(figsize=(15, 10))
sns.heatmap(correlation_matrix, annot=True, cmap='coolwarm', fmt=".2f", linewidths=0.5)
plt.title('Pearson Correlation Coefficients')
plt.show()

In [102]:
highly_correlated_cols = set()
for i in range(len(correlation_matrix.columns)):
    for j in range(i):
        if abs(correlation_matrix.iloc[i, j]) > 0.3:
            colname_i = correlation_matrix.columns[i]
            colname_j = correlation_matrix.columns[j]
            if (colname_i != colname_j) and (colname_i=="zone_047_temp" or colname_j=="zone_047_temp" or colname_i=="hvac_S" or colname_j=="hvac_S"):
                print(colname_i,"----",abs(correlation_matrix.iloc[i, j]),"----",colname_j)
                highly_correlated_cols.add(colname_i)
                highly_correlated_cols.add(colname_j)
                
            

zone_047_fan_spd ---- 0.3838842710385038 ---- zone_047_temp
rtu_004_sa_temp ---- 0.5636316174287519 ---- zone_047_temp
rtu_004_ra_temp ---- 0.32776265464886917 ---- zone_047_temp
rtu_004_oa_temp ---- 0.3911499150089511 ---- zone_047_temp
rtu_004_ma_temp ---- 0.3800818291020465 ---- zone_047_temp
hvac_S ---- 0.3163506114497974 ---- zone_047_hw_valve
hvac_S ---- 0.42500326788919984 ---- rtu_004_fltrd_sa_flow_tn
hvac_S ---- 0.4794994590105312 ---- rtu_004_oa_temp
hvac_S ---- 0.37653522078249596 ---- rtu_004_ma_temp
hvac_S ---- 0.45054590590454646 ---- rtu_004_sf_vfd_spd_fbk_tn
hvac_S ---- 0.3910776435479394 ---- rtu_004_rf_vfd_spd_fbk_tn
aru_001_cwr_temp ---- 0.4337890009515319 ---- zone_047_temp
aru_001_cwr_temp ---- 0.5103744910713975 ---- hvac_S
aru_001_cws_fr_gpm ---- 0.5251959795850137 ---- zone_047_temp
aru_001_cws_fr_gpm ---- 0.4816297584385553 ---- hvac_S
aru_001_cws_temp ---- 0.576461860142355 ---- zone_047_temp
aru_001_cws_temp ---- 0.5060071970556257 ---- hvac_S


In [19]:
final_df = sorted.copy()
final_df['date'] = pd.to_datetime(final_df['date'], format = "%Y-%m-%d %H:%M:%S")
final_df = final_df[ (final_df.date.dt.date >date(2020, 1, 1)) & (final_df.date.dt.date< date(2020, 12, 30))]
final_df.isna().sum()

date                                          0
zone_047_hw_valve                             0
rtu_004_sat_sp_tn                             0
zone_047_temp                                 0
zone_047_fan_spd                              0
rtu_004_fltrd_sa_flow_tn                      0
rtu_004_sa_temp                               0
rtu_004_pa_static_stpt_tn                     0
rtu_004_oa_flow_tn                            0
rtu_004_oadmpr_pct                            0
rtu_004_econ_stpt_tn                          0
rtu_004_ra_temp                               0
rtu_004_oa_temp                               0
rtu_004_ma_temp                               0
rtu_004_sf_vfd_spd_fbk_tn                     0
rtu_004_rf_vfd_spd_fbk_tn                     0
rtu_004_fltrd_gnd_lvl_plenum_press_tn         0
rtu_004_fltrd_lvl2_plenum_press_tn            0
zone_047_cooling_sp                           0
Unnamed: 47_x                                 0
zone_047_heating_sp                     

In [29]:
%matplotlib qt
for i in final_df.columns[11:14]:
    plt.plot(final_df['date'],final_df[i])
plt.show()

In [7]:

dataset = final_df[['rtu_004_oa_temp','rtu_004_ra_temp','hp_hws_temp','rtu_004_ma_temp','rtu_004_sa_temp']].values

# dataset = final_df[['hvac_S','rtu_004_ra_temp','rtu_004_oa_temp','rtu_004_ma_temp','rtu_004_fltrd_sa_flow_tn',
#                     'rtu_004_sf_vfd_spd_fbk_tn','rtu_004_rf_vfd_spd_fbk_tn','zone_047_temp']].values
# dataset = final_df[['rtu_004_fltrd_sa_flow_tn','rtu_004_sf_vfd_spd_fbk_tn','rtu_004_rf_vfd_spd_fbk_tn',
#                     'rtu_004_oa_temp','rtu_004_ma_temp','zone_047_fan_spd','zone_047_hw_valve','rtu_004_sa_temp','zone_047_temp']].values
dataset = dataset.astype('float32')


scaler = MinMaxScaler(feature_range=(0, 1))
dataset = scaler.fit_transform(dataset)
train_size = int(len(dataset)* 0.30)
test_size = len(dataset) - train_size
test,train = dataset[0:train_size,:],dataset[train_size:len(dataset),:]

def create_dataset(dataset,time_step):
    # x1,x2,x3,x4,x5,x6,x7, Y = [],[],[],[],[],[],[],[]
    x1,x2,x3,Y = [],[],[],[]
    for i in range(len(dataset)-time_step-1):
        x1.append(dataset[i:(i+time_step), 0])
        x2.append(dataset[i:(i+time_step), 1])
        x3.append(dataset[i:(i+time_step), 2])
        # x4.append(dataset[i:(i+time_step), 3])
        # x5.append(dataset[i:(i+time_step), 4])
        # x6.append(dataset[i:(i+time_step), 5])
        # x7.append(dataset[i:(i+time_step), 6])
        Y.append([dataset[i + time_step, 3],dataset[i + time_step, 4]])
    # x1,x2,x3,x4,x5,x6,x7,Y =  np.array(x1),np.array(x2),np.array(x3), np.array(x4),np.array(x5),np.array(x6),np.array(x7),np.array(Y)
    x1,x2,x3,Y = np.array(x1),np.array(x2),np.array(x3),np.array(Y)
    # Y = np.reshape(Y,(len(Y),1))
    return np.stack([x1,x2,x3],axis=2),Y




time_step = 60
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)


model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50))
model.add(Dense(units=2))

model.compile(optimizer='adam', loss='mean_squared_error')

model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=64, verbose=1)

train_predict = model.predict(X_train)
test_predict = model.predict(X_test)


c:\Users\jerin\anaconda3\envs\smartbuilding\Lib\site-packages\keras\src\layers\rnn\rnn.py:205: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/2
12174/12174 ━━━━━━━━━━━━━━━━━━━━ 811s 66ms/step - loss: 0.0019 - val_loss: 9.6280e-04
Epoch 2/2
12174/12174 ━━━━━━━━━━━━━━━━━━━━ 814s 67ms/step - loss: 7.9909e-04 - val_loss: 7.6609e-04
24348/24348 ━━━━━━━━━━━━━━━━━━━━ 120s 5ms/step
10434/10434 ━━━━━━━━━━━━━━━━━━━━ 58s 6ms/step


In [18]:
%matplotlib qt

# plt.plot(y_test[:,0], label='Original Testing Data', color='blue')
# plt.plot(test_predict[:,0], label='Predicted Testing Data', color='red')
plt.plot(y_test[:,1], label='Original Testing Data', color='green')
plt.plot(test_predict[:,1], label='Predicted Testing Data', color='orange')
anomalies = np.where(abs(test_predict[:,1] - y_test[:,0]) > 0.5)[0]
plt.scatter(anomalies,test_predict[anomalies,1], color='black',marker ="o",s=100 )
plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

LSTM autoencoder

----------------------------

In [246]:

# dataset = final_df[['zone_047_temp','hvac_S','rtu_004_sa_temp']].values

# dataset = final_df[['hvac_S','rtu_004_ra_temp','rtu_004_oa_temp','rtu_004_ma_temp','rtu_004_fltrd_sa_flow_tn',
#                     'rtu_004_sf_vfd_spd_fbk_tn','rtu_004_rf_vfd_spd_fbk_tn','zone_047_temp']].values
dataset = final_df[['rtu_004_fltrd_sa_flow_tn','rtu_004_sf_vfd_spd_fbk_tn','rtu_004_rf_vfd_spd_fbk_tn',
                    'rtu_004_oa_temp','rtu_004_ma_temp','zone_047_fan_spd','zone_047_hw_valve','rtu_004_ra_temp','rtu_004_sa_temp','zone_047_temp']].values
dataset = dataset.astype('float32')


scaler = MinMaxScaler(feature_range=(0, 1))
dataset = scaler.fit_transform(dataset)
test_size = int(len(dataset)* 0.30)
test, train = dataset[0:test_size,:],dataset[test_size:len(dataset),:]

def create_dataset(dataset,time_step):
    x1,x2,x3,x4,x5,x6,x7,x8,x9, Y = [],[],[],[],[],[],[],[],[],[]

    for i in range(0,len(dataset)-time_step-1):
        x1.append(dataset[i:(i+time_step), 0])
        x2.append(dataset[i:(i+time_step), 1])
        x3.append(dataset[i:(i+time_step), 2])
        x4.append(dataset[i:(i+time_step), 3])
        x5.append(dataset[i:(i+time_step), 4])
        x6.append(dataset[i:(i+time_step), 5])
        x7.append(dataset[i:(i+time_step), 6])
        x8.append(dataset[i:(i+time_step), 7])
        x9.append(dataset[i:(i+time_step), 8])
        Y.append(dataset[i:(i+time_step), 8])
    x1,x2,x3,x4,x5,x6,x7,x8,x9,Y =  np.array(x1),np.array(x2),np.array(x3), np.array(x4),np.array(x5),np.array(x6),np.array(x7),np.array(x8),np.array(x9),np.array(Y)
   
    # Y = np.reshape(Y,(len(Y),1))
    return np.stack([x1,x2,x3,x4,x5,x6,x7,x8,x9],axis=2),Y




time_step = 60
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)


model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
# model.add(LSTM(units=30))
# model.add(Dense(units=time_step))

model.compile(optimizer='adam', loss='mean_squared_error')

# model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=2, batch_size=64, verbose=1)

train_predict = model.predict(X_train)
# test_predict = model.predict(X_test)


c:\Users\jerin\anaconda3\envs\smartbuilding\Lib\site-packages\keras\src\layers\rnn\rnn.py:205: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


11487/24348 ━━━━━━━━━━━━━━━━━━━━ 2:07 10ms/step

: 

In [244]:
X_train.shape

(779111, 60, 9)

In [ ]:
mo

In [241]:
%matplotlib qt
time = 10
mse = (y_test[time] - test_predict[0])**2
anomalies = np.where(mse > 0.0001)[0]
plt.plot(y_test[time], label='Original Data')
plt.plot(test_predict[time], label='predicted Data')
plt.scatter(anomalies,test_predict[time,anomalies], color='red', label='Anomalies')
plt.legend()
plt.show()

In [242]:
model.summary()

Model: "sequential_19"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ lstm_39 (LSTM)                  │ (None, 60, 50)         │        12,000 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_40 (LSTM)                  │ (None, 30)             │         9,720 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_26 (Dense)                │ (None, 60)             │         1,860 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 70,742 (276.34 KB)

 Trainable params: 23,580 (92.11 KB)

 Non-trainable params: 0 (0.00 B)

 Optimizer params: 47,162 (184.23 KB)

In [238]:
test_predict[0]-y_test[0]

array([-0.00162351, -0.00127119, -0.00132501, -0.00043088, -0.00357354,
       -0.00349951, -0.00703096, -0.00679523,  0.00243503,  0.00075096,
        0.015773  ,  0.01411158,  0.01689583,  0.01593572,  0.00665802,
        0.0068891 , -0.001706  , -0.00310844, -0.00871575, -0.00967073,
       -0.00820547, -0.00687617,  0.00930512,  0.00670969,  0.00769156,
        0.01000088, -0.00052458,  0.00010484, -0.00573552, -0.00811213,
       -0.01016176, -0.01063424, -0.01580012, -0.01502603, -0.01243931,
       -0.01488668,  0.00733459,  0.00564003,  0.01374102,  0.01534522,
        0.00324941,  0.00375515, -0.0078848 , -0.00780392, -0.01223874,
       -0.01329106, -0.00772917, -0.00823385,  0.01035273,  0.01039612,
        0.01731664,  0.01493615,  0.00356281,  0.00522107, -0.00680918,
       -0.00461727, -0.00997645, -0.01072395, -0.00542653, -0.00710839],
      dtype=float32)